In [9]:
import socket
import time
print("La bibliothèque socket fonctionne correctement ! va sur https://medium.com/@dantonsa/a-beginner-guide-on-programming-instruments-applying-scpi-protocol-using-python-e415e328cdc1")

La bibliothèque socket fonctionne correctement ! va sur https://medium.com/@dantonsa/a-beginner-guide-on-programming-instruments-applying-scpi-protocol-using-python-e415e328cdc1


In [10]:
# Paramètres de connexion
IP_ADDRESS = "192.168.0.3"
PORT = 5025
NUM_CYCLES = 5  # Nombre de cycles charge/décharge

# Fonctions utilitaires
def send_command(sock, command):
    """Envoie une commande SCPI via une connexion existante."""
    try:
        if sock.fileno() == -1:  # Vérifie si le socket est actif
            print("Le socket est fermé. Reconnexion...")
            sock = reconnect(sock)

        command = command.strip() + "\n"
        sock.sendall(command.encode())
        time.sleep(1)  # Augmentez le délai à 1 seconde
        response = sock.recv(1024).decode().strip()
        print(f"Commande: {command.strip()}\nRéponse: {response}")
        return response
    except BrokenPipeError:
        print("Connexion rompue. Tentative de reconnexion...")
        raise
    except Exception as e:
        print(f"Erreur lors de l'envoi de la commande {command.strip()}: {e}")
        raise

def connect_to_device():
    """Établit une connexion au dispositif."""
    try:
        sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
        sock.settimeout(10)
        sock.setsockopt(socket.SOL_SOCKET, socket.SO_KEEPALIVE, 1)  # Active TCP Keep-Alive
        sock.connect((IP_ADDRESS, PORT))
        print("Connecté à l'alimentation.")
        return sock
    except Exception as e:
        print(f"Erreur lors de la connexion : {e}")
        raise

def reconnect(sock):
    """Rétablit une connexion en cas de perte."""
    try:
        sock.close()
    except:
        pass
    return connect_to_device()
    
def log_device_error(sock):
    """Récupère les erreurs de l'appareil."""
    try:
        error_log = send_command(sock, "SYST:ERR?")
        print(f"Log de l'appareil : {error_log}")
    except Exception as e:
        print(f"Impossible de lire le log de l'appareil : {e}")

def initialize_device(sock):
    """Initialise le dispositif et active le contrôle à distance."""
    # Identification de l'appareil
    response = send_command(sock, "*IDN?")
    if not response:
        raise Exception("Aucune réponse de l'appareil. Vérifiez la connexion.")

    # Activation du contrôle à distance et configuration
    send_command(sock, "SYST:LOCK ON")
    send_command(sock, "SYST:TIMEOUT 0")  # Désactivation du timeout SCPI
    send_command(sock, "*CLS")  # Efface les erreurs précédentes
    send_command(sock, "*RST")  # Réinitialisation de l'appareil

def cycle_charge_discharge(sock):
    """Effectue les cycles de charge et décharge."""
    for cycle in range(1, NUM_CYCLES + 1):
        print(f"\nDébut du cycle {cycle}/{NUM_CYCLES}")
        
        # Étape 1 : Charge
        print("Démarrage de la charge...")
        try:
            time.sleep(0.5)
            send_command(sock, "VOLT 10")
            time.sleep(10)  # Temps de charge

        except BrokenPipeError:
            print("Reconnexion nécessaire pendant la charge.")
            sock = reconnect(sock)
            log_device_error(sock)
            continue

    print("\nTous les cycles sont terminés.")
    send_command(sock, "OUTP:STAT OFF")  # Désactive la sortie

# Script principal
try:
    sock = connect_to_device()
    initialize_device(sock)
    send_command(sock, "OUTP ON")
    cycle_charge_discharge(sock)
except BrokenPipeError:
    print("Erreur critique : Connexion rompue. Tentative de réinitialisation...")
    sock = reconnect(sock)
except Exception as e:
    print(f"Erreur critique : {e}")
finally:
    if sock:
        try:
            send_command(sock, "OUTP OFF")
            send_command(sock, "OUTP:STAT OFF")  # Assurez-vous que l'alimentation est arrêtée
            
        except:
            pass
        sock.close()
        print("Connexion fermée.")



Connecté à l'alimentation.
Commande: *IDN?
Réponse: EA Elektro-Automatik GmbH & Co. KG, ELR 10200-50, 2775120003, V3.03 05.10.2022 V3.06 24.05.2023 V1.0.2.20,
Commande: SYST:LOCK ON
Réponse: 
Commande: SYST:TIMEOUT 0
Réponse: 
Commande: *CLS
Réponse: 
Commande: *RST
Réponse: 
Commande: OUTP ON
Réponse: 

Début du cycle 1/5
Démarrage de la charge...
Commande: VOLT 10
Réponse: 

Début du cycle 2/5
Démarrage de la charge...
Connexion rompue. Tentative de reconnexion...
Reconnexion nécessaire pendant la charge.
Connecté à l'alimentation.
Commande: SYST:ERR?
Réponse: 0,"No error"
Log de l'appareil : 0,"No error"

Début du cycle 3/5
Démarrage de la charge...
Commande: VOLT 10
Réponse: 

Début du cycle 4/5
Démarrage de la charge...
Connexion rompue. Tentative de reconnexion...
Reconnexion nécessaire pendant la charge.
Connecté à l'alimentation.
Commande: SYST:ERR?
Réponse: 0,"No error"
Log de l'appareil : 0,"No error"

Début du cycle 5/5
Démarrage de la charge...
Commande: VOLT 10
Réponse: 

